# Shapefiles 1: Intro to Shapefiles

## Overview:
1. Read in the state/province Natural Earth shapefile
2. Explore the shapefile using GeoPandas
3. Plot the shapefile on a map and overlay with other Natural Earth shapefiles

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Pandas| Necessary | |
| Cartopy| Necessary | |

* **Time to learn**: 30 minutes
***

## What is a **shapefile**?

From [Wikipedia](https://en.wikipedia.org/wiki/Shapefile):
>The shapefile format is a geospatial vector data format for geographic information system (GIS) software. It is developed and regulated by Esri as a mostly open specification for data interoperability among Esri and other GIS software products. The shapefile format can spatially describe vector features: points, lines, and polygons, representing, for example, water wells, rivers, and lakes. Each item usually has attributes that describe it, such as name or temperature.

<div class="alert alert-warning">
    <b>Rasters versus Shapefiles:</b> By virtue of being a *vector data format*, shapefiles do not becoming fuzzy/pixelated as one zooms in on maps that display features defined by shapefiles. This is in contrast to raster-based data. See the first reference at the end of the notebook for a nice explanation.
</div>

<div class="alert alert-info">
    <b>Note:</b> We've already been using shapefiles, whenever we've added various Natural Earth backgrounds with Cartopy's <b>feature</b>. We'll examine shapefiles in more detail here, using Cartopy's <b>shapereader</b>.
</div>

## Imports

In [ ]:
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import geopandas as gp
import matplotlib.pyplot as plt
import pandas as pd
import cartopy.io.shapereader as shpreader
from metpy.plots import USCOUNTIES
import glob
import os

## Read in a shapefile

Use Cartopy's `shpreader.natural_earth` method to read in the highest (10m) resolution states and provinces shapefile. 
It will be automatically downloaded if not present, and is cached by default in a hidden subdirectory in your home directory.

In [ ]:
res = '10m'
category = 'cultural'
name = 'admin_1_states_provinces'
shpfilename = shpreader.natural_earth(res, category, name)
shpfilename

What files matching this particular political boundary classification do we have?

In [ ]:
path = os.path.dirname(shpfilename)
glob.glob(path + "/ne_10m_admin_1_states_provinces.*")

We have five files with different suffixes. The first three **must** be present (see the second reference at the end of the notebook). Here, we will read in the *.shp* file, using a Pandas-like library, **Geopandas**, which creates a geo-referenced Pandas `Dataframe`. 

## Explore the shapefile using [Geopandas](https://geopandas.org/)

Display all columns in the dataframe. Then create the dataframe and take a look at the first and last five rows (scroll to see all 84 columns).

In [ ]:
pd.set_option('display.max_columns', None)
df = gp.read_file(shpfilename)
df

Examine the column names more concisely.

In [ ]:
df.columns

<div class="alert alert-info">
    <b>Tip:</b> Countries are in the DataFrame's <code>admin</code> column. We can chain together Pandas` methods such as <code>sort_values</code> and <code>unique</code> to show all of the countries included in the shapefile.
</div>

In [ ]:
df.admin.sort_values().unique()

Let's display all rows that are in the USA.

In [ ]:
df.loc[df.admin == 'United States of America']

<div class="alert alert-info">
    <b>Tip:</b> The <i>name</i> column corresponds to the states.
</div>

## Examine the *Geometry* column

When Geopandas creates a dataframe from a Shapefile, a key column that gets added is the `geometry` one. Here we can see that each of the states have Geometry features consisting of *Polygons* or *Multipolygons*

In [ ]:
df.loc[df.name == 'Colorado']['geometry']

In [ ]:
df.loc[df.name == 'New York']['geometry']

<div class="alert alert-warning">
    <b>Question:</b> Notice that Colorado's geometry is <i>POLYGON</i> while New York is <i>MULTIPOLYGON</i>. Can you think of a reason for the distinction? (Hint: are any islands part of the state?)
</div>

## Make a Geopandas dataframe for New York State 

In [ ]:
dfNYS = df.loc[df.name == 'New York']

As with any Pandas Dataframe, we can directly call its `plot` method for a quick view.

In [ ]:
dfNYS.plot(figsize=(12,9))

We can create a GeoPandas series consisting only of the Geometry column.

In [ ]:
geoNY = df.loc[df.name == 'New York']['geometry']

In [ ]:
geoNY

Examine the `values` attribute of this Geopandas geometry object:

In [ ]:
geoNY.values

<div class="alert alert-info">
    <b>Note:</b> The object begins with <b>shapely</b>. It stems from the <a href="https://shapely.readthedocs.io/">Shapely</a> library. Although we did not explicitly list this library in our list of imports, it was imported as a result of the <code>import cartopy.io.shapereader as shpreader</code> statement.
</div>

If we take just the first (and only element) of this array, what do we get?

In [ ]:
nysPoly = geoNY.values[0]
nysPoly

## Plot the shapefile

We can now add this object to a Cartopy-referenced Matplotlib plot using Matplotlib's `add_geometries` method.
First we'll comment out all of the Natural Earth shapefiles we typically use. This will produce just a map of NYS.

In [ ]:
fig = plt.figure(figsize=(15,10))
ax = plt.axes(projection=ccrs.PlateCarree())
plt.title('NYS')
ax.add_geometries(nysPoly, ccrs.PlateCarree(),
                  edgecolor='black', facecolor='tab:blue', alpha=0.5)
ax.set_extent([-80, -72,40.5,45.2], ccrs.PlateCarree());

## Add additional features to the plot
Now, add some of Cartopy's Natural Earth features to the plot. We should see that with the exception of the counties (which defaults to a slightly lower resolution (20m) than the others) everything should line up nicely. We'll slightly expand the map extent so we'll see neighboring state/province outlines.

In [ ]:
res = '10m'
fig = plt.figure(figsize=(15,10))
ax = plt.axes(projection=ccrs.PlateCarree())

plt.title('NYS')
ax.coastlines(resolution=res)
ax.add_geometries(nysPoly, ccrs.PlateCarree(),
                  edgecolor='black', facecolor='tab:blue', alpha=0.5)
ax.add_feature (cfeature.LAKES.with_scale(res), alpha = 0.5)
ax.add_feature (cfeature.STATES.with_scale(res))
ax.add_feature(USCOUNTIES,edgecolor='grey',linewidth=1 );
ax.set_extent([-85, -67,37.5,49.5], ccrs.PlateCarree());

<div class="alert alert-info">
    <b>Tip:</b> The USCOUNTIES shapefile also has a 5m version. To use it, append <code>.with_scale('5m')</code> to <code>USCOUNTIES</code>.
</div>

---
## Summary
* Matplotlib and Cartopy, via the Shapely library, provides support for reading and displaying shapefiles. 
* Shapefiles are a form of vector graphics; unlike rasters, they do not degrade as one zooms into them.
* The Geopandas library treats shapefiles as geo-referenced Pandas dataframes.

### What's Next?
We'll return to cloud-optimized geotiffs, specifically those that are tile-based, with more detail automatically displayed as one zooms in to a particular region.

### References:
1. https://www.gislounge.com/geodatabases-explored-vector-and-raster-data/
1. https://www.earthdatascience.org/workshops/gis-open-source-python/intro-vector-data-python/
2. https://wiki.openstreetmap.org/wiki/Shapefiles